# IBM Applied Data Science Capstone Course by Coursera

## Week 5 Final Report

### Opening a new Chinese restaurant in India 

####  (I) Build a dataframe of cities(neighborhoods) in India by web scraping the data from Wikipedia page
####  (II) Get the geographical coordinates of the neighborhoods
####  (III) Obtain the venue data for the neighborhoods from Foursquare API
####  (IV) Explore and cluster the neighborhoods
####  (V) Select the best cluster to open a new chinese restaurant

### 1. Import libraries

In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

!pip install geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

print("Libraries imported.")

     |████████████████████████████████| 102kB 6.9MB/s ta 0:00:011
Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    branca-0.4.0               |             py_0          26 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    openssl-1.1.1f             |       h516909a_0         2.1 MB  conda-forge
    ------------------

### 2. Scrap data from Wikipedia page into a DataFrame

In [133]:
ind_city = pd.read_html('https://en.wikipedia.org/wiki/List_of_cities_in_India_by_population')[0]
ind_city.head(12)

Rank                 City  Population(2011)[3] Population(2001)  \
0      1               Mumbai             12442373         11978450   
1      2                Delhi             11007835          9879172   
2      3            Bangalore              8436675          4301326   
3      4            Hyderabad              6809970          3637483   
4      5            Ahmedabad              5570585          3520085   
5      6              Chennai              4681087          4343645   
6      7              Kolkata              4486679          4572876   
7      8                Surat              4467797          2433835   
8      9                 Pune              3124458          2538473   
9     10               Jaipur              3046163          2322575   
10    11  Visakhapatnam[a][5]              3004086          2412904   
11    12               Kanpur              2765348          2551337   

   State or union territory  
0               Maharashtra  
1                     Delhi  
2                 Karnataka  
3                 Telangana  
4                   Gujarat  
5                Tamil Nadu  
6               West Bengal  
7                   Gujarat  
8               Maharashtra  
9                 Rajasthan  
10           Andhra Pradesh  
11            Uttar Pradesh

In [134]:
ind_city.drop(['Rank','Population(2011)[3]','Population(2001)','State or union territory'], axis=1, inplace=True)
ind_city.head()

City
0     Mumbai
1      Delhi
2  Bangalore
3  Hyderabad
4  Ahmedabad

In [135]:
ind_city.rename(columns = {'City': 'Neighborhood'}, inplace=True)
ind_city.head()

Neighborhood
0       Mumbai
1        Delhi
2    Bangalore
3    Hyderabad
4    Ahmedabad

In [136]:
ind_city.shape

(301, 1)

### 3. Get the geographical coordinates

In [137]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [138]:
coords = [ get_latlng(neighborhood) for neighborhood in ind_city["Neighborhood"].tolist() ]
coords

In [139]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [140]:
# merge the coordinates into the original dataframe
ind_city['Latitude'] = df_coords['Latitude']
ind_city['Longitude'] = df_coords['Longitude']

# check the neighborhoods and the coordinates
print(ind_city.shape)
ind_city.head()

(301, 3)


Neighborhood  Latitude  Longitude
0       Mumbai  18.94017   72.83483
1        Delhi  28.63410   77.21689
2    Bangalore  12.96618   77.58690
3    Hyderabad  17.39487   78.47076
4    Ahmedabad  23.02776   72.60027

In [141]:
# save the DataFrame as CSV file
ind_city.to_csv("ind_city.csv", index=False)

### 4. Create a map of India with neighborhoods superimposed on top

In [142]:
# get the coordinates of India
address = 'India'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of India {}, {}.'.format(latitude, longitude))

The geograpical coordinate of India 22.3511148, 78.6677428.


In [143]:
# create map of India using latitude and longitude values
map_ind = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(ind_city['Latitude'], ind_city['Longitude'], ind_city['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_ind)  
    
map_ind

In [144]:
# save the map as HTML file
map_ind.save('map_ind.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [145]:
# @Hidden cell

# define Foursquare Credentials and Version
CLIENT_ID = 'UEHOMVVWP0KCIDZT0GJIGOQANZZTVHXSNTKMIVRLCS10HZAZ' # your Foursquare ID
CLIENT_SECRET = 'PWYUWA2MR3HUWRUHDLEK1ZB3TFRTCGGR2IYUGRZOLDIKRL0N' # your Foursquare Secret
VERSION = '20200410' # Foursquare API version


#### Now, let's get the top 100 venues that are within a radius of 5000 meters.

In [147]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(ind_city['Latitude'], ind_city['Longitude'], ind_city['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [148]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(5762, 7)


Neighborhood  Latitude  Longitude         VenueName  VenueLatitude  \
0       Mumbai  18.94017   72.83483       Royal China      18.938715   
1       Mumbai  18.94017   72.83483         Starbucks      18.932190   
2       Mumbai  18.94017   72.83483   Britannia & Co.      18.934683   
3       Mumbai  18.94017   72.83483  Wankhede Stadium      18.938792   
4       Mumbai  18.94017   72.83483  Food for Thought      18.932031   

   VenueLongitude       VenueCategory  
0       72.832933  Chinese Restaurant  
1       72.833959         Coffee Shop  
2       72.840183    Parsi Restaurant  
3       72.825944      Cricket Ground  
4       72.831667                Café

#### Let's check how many venues were returned for each neighorhood

In [149]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                                  
Adoni                                4          4          4              4   
Agartala                             8          8          8              8   
Agra                                40         40         40             40   
Ahmedabad                          100        100        100            100   
Ahmednagar                           7          7          7              7   
Aizawl                               6          6          6              6   
Ajmer                               10         10         10             10   
Akola                               10         10         10             10   
Alappuzha                           29         29         29             29   
Aligarh                              4          4          4              4   
Allahabad                           17         17         17             17   
Alwar                                4          4          4              4   
Amaravati                            8          8          8              8   
Ambala                               7          7          7              7   
Ambarnath                           10         10         10             10   
Ambattur                            57         57         57             57   
Amravati                             8          8          8              8   
Amritsar                            46         46         46             46   
Amroha                               3          3          3              3   
Anand                               19         19         19             19   
Anantapur                            4          4          4              4   
Arrah                                5          5          5              5   
Asansol                              5          5          5              5   
Aurangabad                          29         29         29             29   
Aurangabad[35]                      29         29         29             29   
Avadi                                8          8          8              8   
Bahraich                             6          6          6              6   
Ballia                               5          5          5              5   
Bally                                8          8          8              8   
Bangalore                          100        100        100            100   
Baranagar                           22         22         22             22   
Barasat                              4          4          4              4   
Bardhaman                            4          4          4              4   
Bareilly                             4          4          4              4   
Bathinda                             8          8          8              8   
Begusarai                            4          4          4              4   
Belgaum                             24         24         24             24   
Bellary                              7          7          7              7   
Berhampore                           6          6          6              6   
Berhampur                            6          6          6              6   
Bettiah[29]                          4          4          4              4   
Bhagalpur                            4          4          4              4   
Bhalswa Jahangir Pur                22         22         22             22   
Bharatpur                            6          6          6              6   
Bhatpara                             6          6          6              6   
Bhavnagar                           14         14         14             14   
Bhilai                               5          5          5              5   
Bhilwara                             4          4          4              4   
Bhimavaram                           7          7          7              7   
B

#### Let's find out how many unique categories can be curated from all the returned venues

In [150]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 268 uniques categories.


In [151]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Chinese Restaurant', 'Coffee Shop', 'Parsi Restaurant',
       'Cricket Ground', 'Café', 'Scenic Lookout', 'Ice Cream Shop',
       'Seafood Restaurant', 'Art Gallery', 'Indian Restaurant', 'Beach',
       'Boutique', 'History Museum', 'Middle Eastern Restaurant',
       'Asian Restaurant', 'Hotel', 'Breakfast Spot', 'Bar', 'Pub',
       'Italian Restaurant', 'Pizza Place', 'Diner', 'Lounge', 'Market',
       'Dessert Shop', 'Performing Arts Venue', 'Nightclub',
       'New American Restaurant', 'Train Station', 'Deli / Bodega',
       'Monument / Landmark', 'Theater', 'Restaurant', 'Cheese Shop',
       'Brewery', 'General Entertainment', 'Cocktail Bar',
       'Fast Food Restaurant', 'Field', 'Thai Restaurant', 'Flea Market',
       'Music Venue', 'Juice Bar', 'Harbor / Marina', 'Spa',
       'Golf Course', 'Park', 'Steakhouse', 'Club House', 'Bookstore'],
      dtype=object)

In [152]:
# check if the results contain "Chinese Restaurant"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

### 6. Analyze Each Neighborhood

In [153]:
# one hot encoding
ind_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ind_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ind_onehot.columns[-1]] + list(ind_onehot.columns[:-1])
ind_onehot = ind_onehot[fixed_columns]

print(ind_onehot.shape)
ind_onehot.head()

(5762, 269)


Neighborhoods  ATM  Accessories Store  Afghan Restaurant  Airport  \
0        Mumbai    0                  0                  0        0   
1        Mumbai    0                  0                  0        0   
2        Mumbai    0                  0                  0        0   
3        Mumbai    0                  0                  0        0   
4        Mumbai    0                  0                  0        0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Andhra Restaurant  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0                  0       0            0           0                    0   
1                  0       0            0           0                    0   
2                  0       0            0           0                    0   
3                  0       0            0           0                    0   
4                  0       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Auto Dealership  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                0            0          0           0       0     0    0   
1                0            0          0           0       0     0    0   
2                0            0          0           0       0     0    0   
3                0            0          0           0       0     0    0   
4                0            0          0           0       0     0    0   

   Basketball Court  Beach  Bed & Breakfast  Beer Garden  Bengali Restaurant  \
0                 0      0                0            0                   0   
1                 0      0                0            0                   0   
2                 0      0                0            0                   0   
3                 0      0                0            0                   0   
4                 0      0                0            0                   0   

   Big Box Store  Bistro  Board Shop  Boarding House  Boat or Ferry  \
0              0       0           0               0              0   
1              0       0           0               0              0   
2              0       0           0               0              0   
3              0       0           0               0              0   
4              0       0           0               0              0   

   Bookstore  Botanical Garden  Boutique  Bowling Alley  Brazilian Restaurant  \
0          0                 0         0              0                     0   
1          0                 0         0              0                     0   
2          0                 0         0              0                     0   
3          0                 0         0              0                     0   
4          0                 0         0              0                     0   

   Breakfast Spot  Brewery  Buffet  Burger Joint  Burmese Restaurant  \
0               0        0       0             0                   0   
1               0        0       0             0                   0   
2               0        0       0             0                   0   
3               0        0       0             0                   0   
4               0        0  

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [154]:
ind_grouped = ind_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(ind_grouped.shape)
ind_grouped

(296, 269)


Neighborhoods       ATM  Accessories Store  \
0                           Adoni  0.000000           0.000000   
1                        Agartala  0.125000           0.000000   
2                            Agra  0.000000           0.000000   
3                       Ahmedabad  0.000000           0.000000   
4                      Ahmednagar  0.000000           0.000000   
5                          Aizawl  0.000000           0.000000   
6                           Ajmer  0.000000           0.000000   
7                           Akola  0.100000           0.000000   
8                       Alappuzha  0.000000           0.000000   
9                         Aligarh  0.000000           0.000000   
10                      Allahabad  0.000000           0.000000   
11                          Alwar  0.000000           0.000000   
12                      Amaravati  0.000000           0.000000   
13                         Ambala  0.000000           0.000000   
14                      Ambarnath  0.000000           0.000000   
15                       Ambattur  0.000000           0.000000   
16                       Amravati  0.000000           0.000000   
17                       Amritsar  0.000000           0.000000   
18                         Amroha  0.666667           0.000000   
19                          Anand  0.000000           0.000000   
20                      Anantapur  0.000000           0.000000   
21                          Arrah  0.200000           0.000000   
22                        Asansol  0.000000           0.000000   
23                     Aurangabad  0.000000           0.000000   
24                 Aurangabad[35]  0.000000           0.000000   
25                          Avadi  0.000000           0.000000   
26                       Bahraich  0.166667           0.000000   
27                         Ballia  0.400000           0.000000   
28                          Bally  0.000000           0.000000   
29                      Bangalore  0.000000           0.000000   
30                      Baranagar  0.000000           0.000000   
31                        Barasat  0.750000           0.000000   
32                      Bardhaman  0.000000           0.250000   
33                       Bareilly  0.000000           0.250000   
34                       Bathinda  0.000000           0.000000   
35                      Begusarai  0.000000           0.000000   
36                        Belgaum  0.000000           0.000000   
37                        Bellary  0.000000           0.000000   
38                     Berhampore  0.500000           0.000000   
39                      Berhampur  0.500000           0.000000   
40                    Bettiah[29]  0.000000           0.000000   
41                      Bhagalpur  0.000000           0.000000   
42           Bhalswa Jahangir Pur  0.000000           0.000000   
43                      Bharatpur  0.000000           0.000000   
44                       Bhatpara  0.000000           0.000000   
45                      Bhavnagar  0.000000           0.000000   
46                         Bhilai  0.200000           0.000000   
47                       Bhilwara  0.000000           0.000000   
48                     Bhimavaram  0.000000           0.000000   
49                          Bhind  0.333333           0.000000   
50                       Bhiwandi  0.000000           0.000000   
51                        Bhiwani  0.250000           0.000000   
52                         Bhopal  0.000000           0.000000   
53                    Bhubaneswar  0.000000           0.000000   
54                       Bhusawal  0.000000           0.000000   
55                          Bidar  0.166667           0.000000   
56                   Bihar Sharif  0.250000           0.000000   
57                        Bijapur  0.000000           0.000000   
58                        Bikaner  0.000000           0.000000   
59                       Bilaspur  0.000000           0.0000

In [155]:
len(ind_grouped[ind_grouped["Chinese Restaurant"] > 0])

42

#### Create a new DataFrame for Chinese Restaurant data only

In [156]:
ind_ichin = ind_grouped[["Neighborhoods","Chinese Restaurant"]]
ind_ichin.head()

Neighborhoods  Chinese Restaurant
0         Adoni                 0.0
1      Agartala                 0.0
2          Agra                 0.0
3     Ahmedabad                 0.0
4    Ahmednagar                 0.0

In [157]:
ind_ichin.shape

(296, 2)

### 7. Cluster Neighborhoods

In [158]:
# set number of clusters
kclusters = 3

ind_clustering = ind_ichin.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ind_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [159]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
ind_merged = ind_ichin.copy()

# add clustering labels
ind_merged["Cluster Labels"] = kmeans.labels_

In [160]:
ind_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
ind_merged.head()

Neighborhood  Chinese Restaurant  Cluster Labels
0        Adoni                 0.0               0
1     Agartala                 0.0               0
2         Agra                 0.0               0
3    Ahmedabad                 0.0               0
4   Ahmednagar                 0.0               0

In [161]:
# merge ind_grouped with ind_city to add latitude/longitude for each neighborhood
ind_merged = ind_merged.join(ind_city.set_index("Neighborhood"), on="Neighborhood")

print(ind_merged.shape)
ind_merged.head() # check the last columns!

(296, 5)


Neighborhood  Chinese Restaurant  Cluster Labels  Latitude  Longitude
0        Adoni                 0.0               0  15.63333   77.28333
1     Agartala                 0.0               0  23.83145   91.28717
2         Agra                 0.0               0  27.19217   78.00007
3    Ahmedabad                 0.0               0  23.02776   72.60027
4   Ahmednagar                 0.0               0  19.09208   74.73832

In [162]:
# sort the results by Cluster Labels
print(ind_merged.shape)
ind_merged.sort_values(["Cluster Labels"], inplace=True)
ind_merged

(296, 5)


Neighborhood  Chinese Restaurant  Cluster Labels  \
0                           Adoni            0.000000               0   
178                   Miryalaguda            0.000000               0   
179                      Mirzapur            0.000000               0   
180                     Moradabad            0.000000               0   
181                         Morbi            0.000000               0   
182                        Morena            0.000000               0   
183                  Motihari[30]            0.000000               0   
184                        Mumbai            0.010000               0   
185                        Munger            0.000000               0   
186                 Muzaffarnagar            0.000000               0   
187                   Muzaffarpur            0.000000               0   
189                        Nadiad            0.000000               0   
190                     Nagercoil            0.000000               0   
192                       Naihati            0.000000               0   
193                        Nanded            0.000000               0   
177                Mira-Bhayandar            0.000000               0   
194                       Nandyal            0.000000               0   
196                  Narasaraopet            0.000000               0   
197                        Nashik            0.000000               0   
199               Nellore[14][15]            0.000000               0   
201                     Nizamabad            0.000000               0   
202                         Noida            0.000000               0   
203                  North Dumdum            0.000000               0   
204                        Ongole            0.000000               0   
205                          Orai            0.000000               0   
206                     Ozhukarai            0.000000               0   
207                          Pali            0.000000               0   
209                     Panchkula            0.000000               0   
210                      Panihati            0.000000               0   
211                       Panipat            0.000000               0   
212                        Panvel            0.000000               0   
195                   Nangloi Jat            0.000000               0   
213                      Parbhani            0.000000               0   
176                       Mehsana            0.000000               0   
174                           Mau            0.000000               0   
139                     Karaikudi            0.000000               0   
140                 Karawal Nagar            0.000000               0   
141                    Karimnagar            0.000000               0   
142                        Karnal            0.000000               0   
143                       Katihar            0.000000               0   
144                        Kavali            0.000000               0   
145                       Khammam            0.000000               0   
146                       Khandwa            0.000000               0   
294                  Warangal[12]            0.000000               0   
148          Kirari Suleman Nagar            0.000000               0   
150                      Kolhapur            0.000000               0   
153                         Korba            0.000000               0   
154                      Kota[13]            0.000000               0   
156                     Kozhikode            0.000000               0   
175                        Meerut            0.000000               0   
157                         Kulti            0.000000               0   
159                       Kurnool            0.000000               0   
160                         Latur            0.000000               0   
161                          Loni            0.000000               0   
162   

#### Finally, let's visualize the resulting clusters

In [163]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=6)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ind_merged['Latitude'], ind_merged['Longitude'], ind_merged['Neighborhood'], ind_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [164]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

### 8. Examine Clusters

#### Cluster 0

In [165]:
ind_merged.loc[ind_merged['Cluster Labels'] == 0]

Neighborhood  Chinese Restaurant  Cluster Labels  \
0                           Adoni            0.000000               0   
178                   Miryalaguda            0.000000               0   
179                      Mirzapur            0.000000               0   
180                     Moradabad            0.000000               0   
181                         Morbi            0.000000               0   
182                        Morena            0.000000               0   
183                  Motihari[30]            0.000000               0   
184                        Mumbai            0.010000               0   
185                        Munger            0.000000               0   
186                 Muzaffarnagar            0.000000               0   
187                   Muzaffarpur            0.000000               0   
189                        Nadiad            0.000000               0   
190                     Nagercoil            0.000000               0   
192                       Naihati            0.000000               0   
193                        Nanded            0.000000               0   
177                Mira-Bhayandar            0.000000               0   
194                       Nandyal            0.000000               0   
196                  Narasaraopet            0.000000               0   
197                        Nashik            0.000000               0   
199               Nellore[14][15]            0.000000               0   
201                     Nizamabad            0.000000               0   
202                         Noida            0.000000               0   
203                  North Dumdum            0.000000               0   
204                        Ongole            0.000000               0   
205                          Orai            0.000000               0   
206                     Ozhukarai            0.000000               0   
207                          Pali            0.000000               0   
209                     Panchkula            0.000000               0   
210                      Panihati            0.000000               0   
211                       Panipat            0.000000               0   
212                        Panvel            0.000000               0   
195                   Nangloi Jat            0.000000               0   
213                      Parbhani            0.000000               0   
176                       Mehsana            0.000000               0   
174                           Mau            0.000000               0   
139                     Karaikudi            0.000000               0   
140                 Karawal Nagar            0.000000               0   
141                    Karimnagar            0.000000               0   
142                        Karnal            0.000000               0   
143                       Katihar            0.000000               0   
144                        Kavali            0.000000               0   
145                       Khammam            0.000000               0   
146                       Khandwa            0.000000               0   
294                  Warangal[12]            0.000000               0   
148          Kirari Suleman Nagar            0.000000               0   
150                      Kolhapur            0.000000               0   
153                         Korba            0.000000               0   
154                      Kota[13]            0.000000               0   
156                     Kozhikode            0.000000               0   
175                        Meerut            0.000000               0   
157                         Kulti            0.000000               0   
159                       Kurnool            0.000000               0   
160                         Latur            0.000000               0   
161                          Loni            0.000000               0   
162   

#### Cluster 1

In [166]:
ind_merged.loc[ind_merged['Cluster Labels'] == 1]

Neighborhood  Chinese Restaurant  Cluster Labels  Latitude  Longitude
166  Madhyamgram            0.100000               1  22.67097   88.44321
14     Ambarnath            0.100000               1  19.19574   73.19404
120     Jabalpur            0.166667               1  23.17418   79.93136
219    Proddatur            0.111111               1  14.73333   78.55000
290      Vellore            0.076923               1  12.91356   79.13251
151      Kolkata            0.083333               1  22.57053   88.37124
85      Durgapur            0.166667               1  23.48333   87.31667

#### Cluster 2

In [167]:
ind_merged.loc[ind_merged['Cluster Labels'] == 2]

Neighborhood  Chinese Restaurant  Cluster Labels  Latitude  Longitude
274          Thrissur            0.028571               2  10.51082   76.21121
287          Vadodara            0.020408               2  22.30946   73.17993
284        Ulhasnagar            0.047619               2  19.22907   73.16580
136   Kalyan-Dombivli            0.022222               2  19.23246   73.13409
264             Surat            0.058824               2  21.18578   72.83679
149             Kochi            0.021978               2   9.93601   76.26142
152            Kollam            0.029412               2   8.88689   76.59228
155          Kottayam            0.032258               2   9.59477   76.53291
116         Hyderabad            0.020000               2  17.39487   78.47076
106          Guwahati            0.045455               2  26.17724   91.75419
105           Gurgaon            0.020000               2  28.47762   77.06952
188  Mysore[8][9][10]            0.040000               2  12.30906   76.65303
191            Nagpur            0.031915               2  21.15705   79.08217
198       Navi Mumbai            0.030000               2  19.03262   73.02962
200         New Delhi            0.020000               2  28.63095   77.21721
77              Delhi            0.020000               2  28.63410   77.21689
208        Pallavaram            0.020000               2  12.97611   80.18361
70         Coimbatore            0.030000               2  10.99416   76.96629
64         Chandigarh            0.030000               2  30.70341   76.78943
53        Bhubaneswar            0.018519               2  20.26879   85.84100
52             Bhopal            0.029412               2  23.26466   77.40518
240             Salem            0.029412               2  11.66552   78.15164
246      Secunderabad            0.070000               2  17.44200   78.50192
249            Shimla            0.047619               2  31.10321   77.15847
259      South Dumdum            0.045455               2  22.60571   88.39886
262          Srinagar            0.055556               2  34.08443   74.79906
270             Thane            0.030000               2  19.20000   72.96667
215             Patna            0.041667               2  25.60129   85.13751

#### Observations:

Most of the Chinese restaurants are concentrated in the capital cities of states of India, with the highest number in cluster 2 and moderate number in cluster 0. On the other hand, cluster 1 has very low number to totally no chinese restaurants in the neighborhoods. This represents a great opportunity and high potential areas to open new chinese restaurants as there is very little to no competition from restaurants. Meanwhile, chinese restaurants in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of chinese restaurants. From another perspective, this also shows that the oversupply of chinese restaurants mostly happened in the capital cities of the states, with the suburb area still have very few chinese restaurants. Therefore, this project recommends business owners to capitalize on these findings to open new chinese restaurants in neighborhoods in cluster 1 with little to no competition. Business owners with unique selling propositions to stand out from the competition can also open new chinese restaurants in neighborhoods in cluster 0 with moderate competition. Lastly, business owners are advised to avoid neighborhoods in cluster 2 which already have high concentration of restaurants and suffering from intense competition.